In [2]:
import os
import psycopg2
from dotenv import load_dotenv
import ipywidgets as widgets
from IPython.display import display
import pandas as pd

# Laden der Umgebungsvariablen aus lokaler .env-Datei
load_dotenv(".env")

# Verbindungsparameter
DB_HOST = os.getenv("DB_HOST")
DB_PORT = os.getenv("DB_PORT")
DB_NAME = os.getenv("DB_NAME")
DB_USER = os.getenv("DB_USER")
DB_PASS = os.getenv("DB_PASS")

# Dropdown zur Tabellenauswahl
table_dropdown = widgets.Dropdown(
    options=['links', 'media_metadata', 'media_time_series', 'photo_media'],
    description='Tabelle'
)

# Dropdown zur Spaltenauswahl (wird bei Tabellenwechsel dynamisch aktualisiert)
column_dropdown = widgets.Dropdown(
    options=[],
    description='Spalte'
)

# Textfeld für Suchbegriff
search_text = widgets.Text(
    value='',
    description='Suchbegriff'
)

# Button zum Ausführen der Suche
search_button = widgets.Button(
    description='Suchen'
)

# Ausgabe-Bereich für Ergebnisse
output_area = widgets.Output()

def load_columns_for_table(selected_table):
    conn = psycopg2.connect(
        host=DB_HOST,
        port=DB_PORT,
        database=DB_NAME,
        user=DB_USER,
        password=DB_PASS
    )
    try:
        with conn.cursor() as cur:
            cur.execute("""
                SELECT column_name
                FROM information_schema.columns
                WHERE table_name = %s
                ORDER BY ordinal_position
            """, (selected_table,))
            columns = [row[0] for row in cur.fetchall()]
        return columns
    finally:
        conn.close()

def on_table_change(change):
    if change['type'] == 'change' and change['name'] == 'value':
        chosen_table = change['new']
        column_dropdown.options = load_columns_for_table(chosen_table)

table_dropdown.observe(on_table_change)

def execute_search(_):
    output_area.clear_output()
    
    chosen_table = table_dropdown.value
    chosen_column = column_dropdown.value
    chosen_term = search_text.value.strip()
    
    conn = psycopg2.connect(
        host=DB_HOST,
        port=DB_PORT,
        database=DB_NAME,
        user=DB_USER,
        password=DB_PASS
    )
    
    with output_area:
        try:
            with conn.cursor() as cur:
                # Abfrage zur Ermittlung der Gesamtanzahl
                count_query = f"""
                SELECT COUNT(*)
                FROM {chosen_table}
                WHERE {chosen_column} ILIKE %s
                """
                cur.execute(count_query, (f"%{chosen_term}%",))
                total_matches = cur.fetchone()[0]

                # Abfrage der Datensätze (maximal 20)
                data_query = f"""
                SELECT *
                FROM {chosen_table}
                WHERE {chosen_column} ILIKE %s
                LIMIT 20
                """
                cur.execute(data_query, (f"%{chosen_term}%",))
                rows = cur.fetchall()
                col_names = [desc.name for desc in cur.description]

            print(f"Treffer: {total_matches}")

            if rows:
                df = pd.DataFrame(rows, columns=col_names)
                display(df)
            else:
                print("Keine Einträge gefunden.")
        finally:
            conn.close()

search_button.on_click(execute_search)

# Initiales Laden der Spalten des ersten Dropdown-Eintrags
column_dropdown.options = load_columns_for_table(table_dropdown.value)

# Darstellung der Widgets (in einer Box o. Ä. zusammenfassen)
ui = widgets.VBox([table_dropdown, column_dropdown, search_text, search_button, output_area])
display(ui)


In [4]:
def load_photo_media():
    conn = psycopg2.connect(
        host=DB_HOST,
        port=DB_PORT,
        database=DB_NAME,
        user=DB_USER,
        password=DB_PASS
    )
    try:
        with conn.cursor() as cur:
            # Keine Limitierung, um alle Einträge zu laden
            query = "SELECT * FROM photo_media"
            cur.execute(query)
            rows = cur.fetchall()
            col_names = [desc.name for desc in cur.description]
            df = pd.DataFrame(rows, columns=col_names)
            return df
    finally:
        conn.close()

# Laden der gesamten Tabelle und Anzeige des DataFrames
df_photo_media = load_photo_media()
display(df_photo_media)

id                                                url  \
0      7453990025647148310  https://www.tiktok.com/@quaschquality/video/74...   
1      7453982466777304342  https://www.tiktok.com/@quaschquality/video/74...   
2      7453742716233551127  https://www.tiktok.com/@quaschquality/video/74...   
3      7453396322977074454  https://www.tiktok.com/@quaschquality/video/74...   
4      7453163604150422806  https://www.tiktok.com/@quaschquality/video/74...   
...                    ...                                                ...   
97773  7457866054581177622  https://www.tiktok.com/@quaschquality/video/74...   
97774  7456457533562277142  https://www.tiktok.com/@quaschquality/video/74...   
97775  7456387296825216278  https://www.tiktok.com/@quaschquality/video/74...   
97776  7455476707814952214  https://www.tiktok.com/@quaschquality/video/74...   
97777  7455053374367616278  https://www.tiktok.com/@quaschquality/video/74...   

                                                   title  \
0      Wahlprognosen zur Bundestagswahl 2025... #demo...   
1      #erinnerung Alice Weidel... #gerechtigkeit #fy...   
2      #erinnerung Alice Weidel,AfD #aliceweidel #dem...   
3      Weidel Ja oder Nein ‼️#gerechtigkeit #viral #f...   
4      Kindergeld... #afd #gerechtigkeit #demokratie ...   
...                                                  ...   
97773  Bitte seit Dabei.. #elonmusk #aliceweidel #afd...   
97774  Es wird Blau 23.02.2025... #afddeuschland #afd...   
97775  Steht auf... #afddeuschland #afd #viral #fyp #...   
97776  So ist es... 2025 #fyp #afd #gerechtigkeit #vi...   
97777  Windräder... #demokratie #quatschstrudel #afdd...   

                                             description  duration  \
0      Wahlprognosen zur Bundestagswahl 2025... #demo...      45.0   
1      #erinnerung Alice Weidel... #gerechtigkeit #fy...      37.0   
2      #erinnerung Alice Weidel,AfD #aliceweidel #dem...      85.0   
3      Weidel Ja oder Nein ‼️#gerechtigkeit #viral #f...       5.0   
4      Kindergeld... #afd #gerechtigkeit #demokratie ...      50.0   
...                                                  ...       ...   
97773  Bitte seit Dabei.. #elonmusk #aliceweidel #afd...      10.0   
97774  Es wird Blau 23.02.2025... #afddeuschland #afd...      15.0   
97775  Steht auf... #afddeuschland #afd #viral #fyp #...      33.0   
97776  So ist es... 2025 #fyp #afd #gerechtigkeit #vi...     131.0   
97777  Windräder... #demokratie #quatschstrudel #afdd...      32.0   

       view_count  like_count  repost_count  comment_count       uploader  \
0            3760         242             0             14  quaschquality   
1             657         127             0             12  quaschquality   
2             915         212             7             18  quaschquality   
3           11800        2544            18            777  quaschquality   
4            1734         192             1             19  quaschquality   
...           ...         ...           ...            ...            ...   
97773         613          66             0              6  quaschquality   
97774         776         125             1             13  quaschquality   
97775         732         101             0              8  quaschquality   
97776        1586         187             0              9  quaschquality   
97777        1063         125             0              7  quaschquality   

       ...   timestamp extractor classification  \
0      ...  1735517304      None          photo   
1      ...  1735515540      None        unknown   
2      ...  1735459726      None        unknown   
3      ...  1735379071      None        unknown   
4      ...  1735324883      None          photo   
...    ...         ...       ...            ...   
97773  ...  1736419761      None        unknown   
97774  ...  1736091811      None        unknown   
97775  ...  1736075459      None          photo   
97776  ...  1735863451      None          photo   
977

In [14]:
# Anzeigen der ersten 200 Zeilen des DataFrames
df_photo_media_first_200 = df_photo_media.head(200)

In [15]:
# Anzeigen der ersten 200 Zeilen des DataFrames
df_photo_media.head(200)

id                                                url  \
0    7453990025647148310  https://www.tiktok.com/@quaschquality/video/74...   
1    7453982466777304342  https://www.tiktok.com/@quaschquality/video/74...   
2    7453742716233551127  https://www.tiktok.com/@quaschquality/video/74...   
3    7453396322977074454  https://www.tiktok.com/@quaschquality/video/74...   
4    7453163604150422806  https://www.tiktok.com/@quaschquality/video/74...   
..                   ...                                                ...   
195  7459143844366486806  https://www.tiktok.com/@poseidon20243/video/74...   
196  7459136840117898518  https://www.tiktok.com/@poseidon20243/video/74...   
197  7459072544105139478  https://www.tiktok.com/@poseidon20243/video/74...   
198  7458944456750812438  https://www.tiktok.com/@poseidon20243/video/74...   
199  7458798195234196769  https://www.tiktok.com/@poseidon20243/video/74...   

                                                 title  \
0    Wahlprognosen zur Bundestagswahl 2025... #demo...   
1    #erinnerung Alice Weidel... #gerechtigkeit #fy...   
2    #erinnerung Alice Weidel,AfD #aliceweidel #dem...   
3    Weidel Ja oder Nein ‼️#gerechtigkeit #viral #f...   
4    Kindergeld... #afd #gerechtigkeit #demokratie ...   
..                                                 ...   
195                                       Poseidon 💙💙💙   
196                                    Poseidon 🇩🇪🇩🇪🇩🇪   
197                                Poseidon   🇩🇪🇩🇪🇩🇪🇩🇪   
198                                    Poseidon 🇩🇪🇩🇪🇩🇪   
199                                    Poseidon 🇩🇪🇩🇪🇩🇪   

                                           description  duration  view_count  \
0    Wahlprognosen zur Bundestagswahl 2025... #demo...      45.0        3760   
1    #erinnerung Alice Weidel... #gerechtigkeit #fy...      37.0         657   
2    #erinnerung Alice Weidel,AfD #aliceweidel #dem...      85.0         915   
3    Weidel Ja oder Nein ‼️#gerechtigkeit #viral #f...       5.0       11800   
4    Kindergeld... #afd #gerechtigkeit #demokratie ...      50.0        1734   
..                                                 ...       ...         ...   
195                                       Poseidon 💙💙💙      55.0        1793   
196                                    Poseidon 🇩🇪🇩🇪🇩🇪      51.0        5179   
197                                Poseidon   🇩🇪🇩🇪🇩🇪🇩🇪      22.0       12700   
198                                    Poseidon 🇩🇪🇩🇪🇩🇪      87.0         873   
199                                    Poseidon 🇩🇪🇩🇪🇩🇪      87.0        1142   

     like_count  repost_count  comment_count       uploader  ...  \
0           242             0             14  quaschquality  ...   
1           127             0             12  quaschquality  ...   
2           212             7             18  quaschquality  ...   
3          2544            18            777  quaschquality  ...   
4           192             1             19  quaschquality  ...   
..          ...           ...            ...            ...  ...   
195         318             6             54  poseidon20243  ...   
196         819            33            114  poseidon20243  ...   
197        3209           171            365  poseidon20243  ...   
198         140             0             13  poseidon20243  ...   
199         264             3             48  poseidon20243  ...   

                          artists   timestamp extractor classification  \
0           Андрей Золотой Дракон  1735517304      None          photo   
1              Ⓜ️r.QᵁᴬᵀˢᶜᴴSᵀᴿᵁᴰᴱᴸ  1735515540      None        unknown   
2              Ⓜ️r.QᵁᴬᵀˢᶜᴴSᵀᴿᵁᴰᴱᴸ  1735459726      None        unknown   
3                    DkTemplateCC  1735379071      None        unknown   
4    Electronic Dance Music [EDM]  1735324883      None          photo   
..                            ...         ...       ...            ...   
195               Jordan Tilstone  1736717268      None          photo   
196   

In [16]:
import pandas as pd

# Maximale Anzahl der Zeilen, die Pandas anzeigt. Setzen Sie auf None, um alles anzuzeigen
pd.set_option('display.max_rows', None)

# Maximale Anzahl der Zeichen in jeder Spalte anzeigen
pd.set_option('display.max_colwidth', None)

# Alternative, um breitere Tabellen besser zu handhaben:
pd.set_option('display.width', None)

# Anzeigen der ersten 200 Zeilen
df_photo_media.head(200)

id  \
0    7453990025647148310   
1    7453982466777304342   
2    7453742716233551127   
3    7453396322977074454   
4    7453163604150422806   
5    7453089543281970454   
6    7452802509275499798   
7    7452025257931590934   
8    7451556309716995351   
9    7451553205332249878   
10   7451333920160894230   
11   7451217562513280278   
12   7449531214345669910   
13   7448663176394198294   
14   7448374225389243670   
15   7448339021899582742   
16   7447430169503042838   
17   7445987962602409238   
18   7445595593268808982   
19   7444927513400200470   
20   7444858037589789974   
21   7444830890716417302   
22   7444507582666001686   
23   7444245445938826518   
24   7442626272796134678   
25   7441517918313139478   
26   7441010856235732246   
27   7440861085155986710   
28   7440183878003789078   
29   7439652462656507168   
30   7438496244932087072   
31   7438257337044864289   
32   7437598865789898017   
33   7437494164142460193   
34   7436514135241755936   
35   7436443633634512160   
36   7436090158161628448   
37   7435663939741961505   
38   7435652521089043745   
39   7434955950831783201   
40   7434646576120827168   
41   7434616633991122208   
42   7434327748698524960   
43   7434279934283025696   
44   7434210241572654368   
45   7434133114663816481   
46   7433952773776919841   
47   7433870459625557281   
48   7433756277504855329   
49   7433546206321593632   
50   7433535553858981152   
51   7433107060109200673   
52   7433104133315382561   
53   7433103607311912225   
54   7432451459280588064   
55   7431928296318831905   
56   7431883175426559264   
57   7431475594942041376   
58   7431250848702876961   
59   7430132392079166753   
60   7429394664324599072   
61   7428903318719614241   
62   7428578017301056801   
63   7427671843248688416   
64   7427543395054161184   
65   7426840667172867360   
66   7426144741449862433   
67   7421529341869247776   
68   7420819716811410721   
69   7420784142373129505   
70   7420019699737480480   
71   7419467031512124705   
72   7417519351206579489   
73   7416383044866657568   
74   7411835810422492448   
75   7409953324365057313   
76   7408977689324948768   
77   7408905144307289376   
78   7408287734348959009   
79   7408198020837264672   
80   7407333185371016481   
81   7407097755002260769   
82   7407004857057512736   
83   7406009932635508001   
84   7400881986308427040   
85   7348679680284773664   
86   7268947238070619424   
87   7468740436488654102   
88   7468732427121249558   
89   7468404620075732246   
90   7468401796487154966   
91   7398714841977867552   
92   7468377277978414338   
93   7468375584767380758   
94   7468370748286029078   
95   7468366856470957334   
96   7467923234298825986   
97   7467600793672092950   
98   7465259162180635926   
99   7467584831598218518   
100  7467581914443123970   
101  7467326481362996502   
102  7467268441171381526   
103  7467266846421519638   
104  7467254258803461398   
105  7465384358392696087   
106  7467190839626779926   
107  7465794027699358998   
108  7465782935988243734   
109  7465782806199684374   
110  7465714348116282646   
111  7465710859927489814   
112  7465614703935376662   
113  7465424939286564118   
114  7465415410486136086   
115  7465392131780185366   
116  7465389780528844054   
117  7465062293492010263   
118  7465048816119516438   
119  7465045677546949910   
120  7465025014044052758   
121  7465011967950998806   
122  7464618080681889046   
123  7464989336501587222   
124  7464879548585217302   
125  7464872284071709974   
126  7464866786526154006   
127  7464667708655963394   
128  7464663490213514518   
129  7464655397949820182   
130  7464617827849309462   
131  7464523372852972822   
132  7464523124281822486   
133  7464260112971238679   
134  7464257920167955734   
135  7461542293040909590   
136  7460798506173844768   
137  7461541000134069536   
138  7461404382794501398   
139  7461371166851222806   
140  7461368366033325334   
141  7461367425716505878   
142  7461359121535